# Whole-genome analysis workflow

In [1]:
# ~2 minutes to install 
#%pip install -U --no-cache-dir scikit-learn scikit-optimize prefect prefect-ray ray plotly openpyxl shap lion_pytorch pytorch_tabnet xgboost neptune pyspark pyarrow dill fastnumbers

In [3]:
from prefect import task, flow
from prefect.task_runners import ConcurrentTaskRunner
from prefect_ray.task_runners import RayTaskRunner
from DillSerializer import DillSerializer
import ray

import pandas as pd
import numpy as np

import logging

!export PREFECT_LOGGING_LEVEL="WARNING"
ray.shutdown()
parallelRunner = ray.init(
  configure_logging=True,
  logging_level=logging.ERROR,
)
parallelRunner

RayContext(dashboard_url='', python_version='3.10.10', ray_version='2.3.1', ray_commit='5f14cee8dfc6d61ec4fd3bc2c440f9944e92b33a', address_info={'node_ip_address': '192.168.1.107', 'raylet_ip_address': '192.168.1.107', 'redis_address': None, 'object_store_address': '/tmp/ray/session_2023-06-05_16-41-22_451157_36436/sockets/plasma_store', 'raylet_socket_name': '/tmp/ray/session_2023-06-05_16-41-22_451157_36436/sockets/raylet', 'webui_url': '', 'session_dir': '/tmp/ray/session_2023-06-05_16-41-22_451157_36436', 'metrics_export_port': 59791, 'gcs_address': '192.168.1.107:59594', 'address': '192.168.1.107:59594', 'dashboard_agent_listen_port': 52365, 'node_id': 'c219cb799df51c818d6624e6cc3e9872ea753c8cdb0f9335c6df5103'})

In [12]:
from sklearn.ensemble import (
    AdaBoostClassifier,
    RandomForestClassifier,
)
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import MultinomialNB
from sklearn.svm import LinearSVC, SVC
from xgboost import XGBClassifier
from pytorch_tabnet.tab_model import TabNetClassifier
from lion_pytorch import Lion

from skopt.space import Categorical, Integer, Real

from env import neptune_api_token

RadialBasisSVC = SVC
RadialBasisSVC.__name__ = "RadialBasisSVC"

clearHistory = True
config = {
  'vcfLike': {  
    'path': 'Variant_report_NUPs_fixed_2022-03-28.xlsx',             # variant call table with annotations
    'sheet': "all cases vs all controls",                             # sheet name if Excel spreadsheet
    'indexColumn': ['chrom', 'position', 'Gene'],       # header that indexes variants (set as list with multiple columns)
    'binarize': False,                           # binarize variants to 0/1, or sum to weigh allele frequency
    'minAlleleFrequency': 0.05,           # filter out variants with allele frequency less than this
  # 'alleleModel': ['dominant', 'recessive', 'overDominant'],  # biallelic allele models to test on gene sets
    'filters': {
      } 
  }, # TODO handle genotypes from related individuals
  
  'geneSets' : { # TODO gene sets
      },
  
  'tracking': {
    'name': 'Nucleoporin genes', # name of the experiment
    'entity': 'ejmockler',
    'project': 'ALS-NUPS-NonBinarized',
    'plotAllSampleImportances': True,  # if calculating Shapely explanations, plot each sample in Neptune
    'token': neptune_api_token
  },

  'clinicalTable': {
      'path': 'ACWM.xlsx',                      # clinical data as Excel spreadsheet
      'idColumn': 'ExternalSampleId',           # genotype ID header
      'uniqueIdColumn': 'ExternalSubjectId',    # unique ID for each patient
      'labelColumn': 'Subject Group',                # header that has case/control labels
      'controlLabels': ['Non-Neurological Control'], # these labels include external sample IDs (like 1000 Genomes)
      'caseLabels': ['ALS Spectrum MND'],
      'controlAlias': 'control',
      'caseAlias': 'case',
      'filters': 'pct_european>=0.85',             # filter out nonhomogenous samples with less than 85% European ancestry
  },

  'externalTables': {
      'path': ['igsr-1000 genomes phase 3 release.tsv'],  # external sample table
      'label': ['control'], # case | control | mixed (mixed labels are held out as an external test set)
      'idColumn': ['Sample name'],                        # sample ID header
      'filters': ["`Superpopulation code`=='EUR' & `Population name`!='Finnish'"], # remove finnish samples due to unusual homogeneity (verify w/ PCA)
  },

  'sampling': {
    'bootstrapIterations': 60, 
    'crossValIterations': 10,   # number of validations per bootstrap iteration
    'holdoutSplit': 0.1,
  },
  
  'model': {
    'stack': {
      LinearSVC(): {
            "tol": Real(1e-6, 1e+1, prior="log-uniform"),
            "C": Real(1e-4, 1e+1, prior="log-uniform"),
        },
      RadialBasisSVC(probability=True, kernel="rbf"): {
          "tol": Real(1e-4, 1e+1, prior="log-uniform"),
          "C": Real(1e-4, 1e+1, prior="log-uniform"),
          "gamma": Categorical(["scale", "auto"]),
      },
      LogisticRegression(penalty="l2", solver="saga"): {
          "tol": Real(1e-6, 1e+1, prior="log-uniform"),
          "C": Real(1e-4, 1e+1, prior="log-uniform"),
      },
      MultinomialNB(): {"alpha": Real(1e-10, 1e+1, prior="log-uniform")},
      AdaBoostClassifier(): {
          "n_estimators": Integer(25, 75),
          "learning_rate": Real(1e-6, 1e+1, prior="log-uniform"),
      },
      XGBClassifier(): {
          "learning_rate": Real(1e-6, 1e+1, prior="log-uniform"),
          "n_estimators": Integer(10, 100),
      },
      RandomForestClassifier(): { 
          "n_estimators": Integer(75, 200),
      },
    },
    'hyperparameterOptimization': False,
    'calculateShapelyExplanations': False,
  }
}
 
async def remove_all_flows():
  from prefect.client import get_client
  orion_client = get_client()
  flows = await orion_client.read_flows()
  for flow in flows:
    flow_id = flow.id
    print(f"Deleting flow: {flow.name}, {flow_id}")
    await orion_client._client.delete(f"/flows/{flow_id}")
    print(f"Flow with UUID {flow_id} deleted")

if clearHistory: await remove_all_flows()

Deleting flow: bootstrapSampling, 4874c584-62c0-4157-9e38-0cc2b5cbbf7e
Flow with UUID 4874c584-62c0-4157-9e38-0cc2b5cbbf7e deleted
Deleting flow: classify, 23c7f34d-a236-4358-8b58-247c429f41a4
Flow with UUID 23c7f34d-a236-4358-8b58-247c429f41a4 deleted
Deleting flow: evaluate, 66eb5fd2-e162-4840-9fcf-ace8a1ca4295
Flow with UUID 66eb5fd2-e162-4840-9fcf-ace8a1ca4295 deleted
Deleting flow: processInputFiles, d4605669-6efc-40bd-9b96-32fb1ea39d8f
Flow with UUID d4605669-6efc-40bd-9b96-32fb1ea39d8f deleted
Deleting flow: trackVisualizations, 3583dda2-b393-4f1b-b6cc-5e8ad1a1f756
Flow with UUID 3583dda2-b393-4f1b-b6cc-5e8ad1a1f756 deleted


In [13]:
from prefect import unmapped
from tqdm import tqdm

@task()
def filterTable(table, filterString):
    if not filterString: return table
    print(f"Filtering: {filterString}")
    filteredTable = table.query(filterString)
    return filteredTable

@task()
def applyAlleleModel(values, columns, genotypeIDs):
    # some genotype IDs are subset of column names (or vice versa)
    genotypeDict = dict()
    resolvedGenotypeIDs = set()
    for id in tqdm(genotypeIDs, unit='id'):
        for j, column in enumerate(columns):
            if id in column or column in id:
                # implement allele model
                genotypeDict[f"{column}"] = [(
                                np.sum([int(allele) for allele in genotype.replace("'", "").split("/")]) # split by allele delimiter 
                                if not config["vcfLike"]["binarize"] 
                                else np.clip(
                                        np.sum([int(allele) for allele in genotype.replace("'", "").split("/")]), 
                                        a_max=1, a_min=None)
                                )
                            if any(char.isdigit() for char in genotype)
                            else np.nan
                            for genotype in values[:,j]
                        ]
                columns = np.delete(columns, j)
                values = np.delete(values, j, axis=1)
                resolvedGenotypeIDs.update({id})
                break
    missingGenotypeIDs = set(genotypeIDs) - resolvedGenotypeIDs  # leftover columns are missing
    return genotypeDict, missingGenotypeIDs, resolvedGenotypeIDs

@task()
def load():
    clinicalData = pd.read_excel(config['clinicalTable']['path'], index_col=config['clinicalTable']['idColumn']
                                ).drop_duplicates(subset=config['clinicalTable']['uniqueIdColumn'])
    externalSamples = [pd.read_csv(path, sep='\t', index_col=idColumn) for path, idColumn in zip(config['externalTables']['path'], config['externalTables']['idColumn'])]
    annotatedVCF = pd.read_csv(
        config['vcfLike']['path'], sep='\t', dtype=str, index_col=config['vcfLike']['indexColumn'], 
        ) if "xlsx" not in config['vcfLike']['path'] else pd.read_excel(
            config['vcfLike']['path'], sheet_name=(config['vcfLike']['sheet'] if config['vcfLike']['sheet'] else None), 
            dtype=str, na_values=['.'], keep_default_na=False
        )
    # remove null chromosome positions
    annotatedVCF[config['vcfLike']['indexColumn']] = annotatedVCF[config['vcfLike']['indexColumn']].astype(str).replace('', np.nan)
    return clinicalData, externalSamples, annotatedVCF.dropna(subset=config['vcfLike']['indexColumn']).set_index(config['vcfLike']['indexColumn'])

@flow(task_runner=ConcurrentTaskRunner(), log_prints=True)
async def processInputFiles():
    clinicalData, externalSamples, annotatedVCF = load()
    
    filteredClinicalData = filterTable(clinicalData, config['clinicalTable']['filters'])
    print(f"filtered {len(clinicalData) - len(filteredClinicalData)} samples from clinical data")
    filteredExternalSamples = [filterTable(externalSampleTable, filterString) for externalSampleTable, filterString in zip(externalSamples, config['externalTables']['filters'])]
    for i, (externalSampleTable, path) in enumerate(zip(filteredExternalSamples, config['externalTables']['path'])):
        print(f"filtered {len(externalSamples[i]) - len(externalSampleTable)} samples from external data {path}")
    filteredVCF = filterTable(annotatedVCF, config['vcfLike']['filters'])
    print(f"filtered {annotatedVCF.shape[0] - filteredVCF.shape[0]} variants from VCF")
    
    caseIDsMask, controlIDsMask = [
        filteredClinicalData[config['clinicalTable']['labelColumn']].isin(labels).dropna()
        for labels in (config['clinicalTable']['caseLabels'], config['clinicalTable']['controlLabels'])]
    
    caseIDs = caseIDsMask[caseIDsMask].index.to_numpy()
    controlIDs = controlIDsMask[controlIDsMask].index.to_numpy()
    for i, label in enumerate(config['externalTables']['label']):
        if label == config['clinicalTable']['caseAlias']:
            caseIDs = np.append(caseIDs, filteredExternalSamples[i].index.to_numpy())
        elif label == config['clinicalTable']['controlAlias']:
            controlIDs = np.append(controlIDs, filteredExternalSamples[i].index.to_numpy())

    # cast genotypes as numeric, drop chromosome positions with missing values
    caseGenotypeFutures, controlGenotypeFutures = applyAlleleModel.map(
            unmapped(filteredVCF.to_numpy()),
            unmapped(filteredVCF.columns.to_numpy()), 
            genotypeIDs=[IDs for IDs in (caseIDs, controlIDs)]
        ) 
    caseGenotypeDict, missingCaseIDs, resolvedCaseIDs = caseGenotypeFutures.result()
    controlGenotypeDict, missingControlIDs, resolvedControlIDs = controlGenotypeFutures.result()
    
    if len(missingCaseIDs) > 0 or len(missingControlIDs) > 0:
        for alias, IDs in {"caseAlias": missingCaseIDs, "controlAlias": missingControlIDs}.items():
            print(f"\nmissing {len(IDs)} {config['clinicalTable'][alias]} IDs:\n {IDs}")
    caseGenotypes = pd.DataFrame.from_dict(caseGenotypeDict)
    caseGenotypes.index.name = filteredVCF.index.name
    caseGenotypes.index = filteredVCF.index
    controlGenotypes = pd.DataFrame.from_dict(controlGenotypeDict)
    controlGenotypes.index.name = filteredVCF.index.name
    controlGenotypes.index = filteredVCF.index
    
    caseIDs = resolvedCaseIDs
    controlIDs = resolvedControlIDs
    
    print(f"\n{len(caseIDs)} cases:\n {caseIDs}")
    print(f"\n{len(controlIDs)} controls:\n {controlIDs}")
    # filter allele frequencies
    allGenotypes = pd.concat([caseGenotypes.dropna(how='any', axis=0), controlGenotypes.dropna(how='any', axis=0)], axis=1)
    filteredGenotypes = allGenotypes.loc[
        allGenotypes.gt(0).sum(axis=1).divide(len(allGenotypes.columns)) >= config['vcfLike']['minAlleleFrequency']]
    print(f"Filtered {len(filteredVCF) - len(filteredGenotypes)} alleles with frequency below {'{:.3%}'.format(config['vcfLike']['minAlleleFrequency'])}")
    print(f"Kept {len(filteredGenotypes)} alleles")
    
    caseGenotypes = filteredGenotypes.loc[:,caseGenotypes.columns]
    controlGenotypes = filteredGenotypes.loc[:,controlGenotypes.columns]
    
    return [caseGenotypes, caseIDs, controlGenotypes, controlIDs, filteredClinicalData]

caseGenotypes, caseIDs, controlGenotypes, controlIDs, clinicalData = await processInputFiles()
print(f"\nclinical data:\n{clinicalData.head()}")

17:51:30.820 | INFO    | prefect.engine - Created flow run 'agile-piculet' for flow 'processInputFiles'

17:51:30.899 | INFO    | Flow run 'agile-piculet' - Created task run 'load-0' for task 'load'

17:51:30.901 | INFO    | Flow run 'agile-piculet' - Executing 'load-0' immediately...

/home/noot/.pyenv/versions/miniconda3-latest/lib/python3.10/site-packages/openpyxl/worksheet/_reader.py:329: UserWarning:

Unknown extension is not supported and will be removed



17:52:40.270 | INFO    | Task run 'load-0' - Finished in state Completed()

...

17:54:45.620 | INFO    | Flow run 'agile-piculet' - 
684 controls:
 {'HG01527', 'HG01504', 'CGND-HDA-03739', 'CGND-HDA-03468', 'CGND-HDA-03545', 'HG01522', 'CGND-HDA-04090', 'CGND-HDA-03771', 'HG00099', 'NA06984', 'HG00243', 'CGND-HDA-01486', 'NA20801', 'CGND-HDA-02738', 'NA20544', 'CGND-HDA-03459', 'HG01510', 'HG00113', 'CGND-HDA-02515', 'HG01670', 'HG00263', 'CGND-HDA-02758', 'NA11831', 'CGND-HDA-03783', 'NA12842', 'NA20534', 'HG00123', 'CGND-HDA-01640', 'CGND-HDA-03772', 'NA11829', 'CGND-HDA-02726', 'HG02223', 'NA20754', 'NA12347', 'NA12873', 'NA12827', 'HG01617', 'HG00108', 'HG00097', 'CGND-HDA-01501', 'NA12717', 'NA12751', 'CGND-HDA-02518', 'CGND-HDA-03811', 'CGND-HDA-01522', 'NA20792', 'HG01669', 'NA20582', 'CGND-HDA-03795', 'HG00126', 'HG00237', 'HG00133', 'NA11843', 'CGND-HDA-02512', 'CGND-HDA-03103', 'HG01768', 'NA12874', 'NA20509', 'CGND-HDA-03532', 'CGND-HDA-02740', 'CGND-HDA-01436', 'HG00102', 'NA20828', 'HG01777', 'CGND-HDA-03797', 'NA20821', 'NA12348', 'HG01699', 'HG00159', 'NA12889', 'CGND-HDA-02714', 'CGND-HDA-01487', 'CGND-HDA-01425', 'NA20519', 'NA12762', 'NA20775', 'HG01525', 'CGND-HDA-01484', 'CGND-HDA-01641', 'CGND-HDA-03520', 'HG01702', 'NA07000', 'HG01790', 'CGND-HDA-03035', 'CGND-HDA-02510', 'NA12413', 'CGND-HDA-03951', 'NA11830', 'CGND-HDA-00435', 'HG00115', 'CGND-HDA-03093', 'CGND-HDA-02830', 'NA20770', 'CGND-HDA-01901', 'NA12156', 'NA20814', 'CGND-HDA-02748', 'NA20768', 'NA20771', 'HG01632', 'NA20505', 'HG00251', 'CGND-HDA-01653', 'HG02221', 'CGND-HDA-01852', 'NA07037', 'HG00125', 'CGND-HDA-00599', 'NA20783', 'CGND-HDA-01414', 'NA20760', 'CGND-HDA-01426', 'CGND-HDA-02444', 'CGND-HDA-03669', 'HG01767', 'HG00109', 'HG00254', 'CGND-HDA-03075', 'HG00242', 'CGND-HDA-03152', 'HG01623', 'NA20796', 'CGND-HDA-02223', 'HG00111', 'CGND-HDA-00209', 'CGND-HDA-03778', 'CGND-HDA-03794', 'CGND-HDA-03448', 'CGND-HDA-01438', 'HG00238', 'HG01521', 'NA12286', 'CGND-HDA-03137', 'NA12249', 'NA20524', 'HG01503', 'NA20790', 'NA12813', 'CGND-HDA-01607', 'NA12812', 'HG00231', 'CGND-HDA-01557', 'HG01513', 'HG01707', 'CGND-HDA-01500', 'NA12718', 'HG02239', 'CGND-HDA-03734', 'CGND-HDA-02724', 'NA20818', 'CGND-HDA-02760', 'NA20512', 'HG00265', 'NA12763', 'CGND-HDA-01655', 'NA12043', 'CGND-HDA-03770', 'CGND-HDA-02530', 'CGND-HDA-01929', 'NA11994', 'HG00155', 'NA20516', 'CGND-HDA-03487', 'HG01605', 'HG01779', 'NA20799', 'HG00110', 'CGND-HDA-03584', 'HG00140', 'NA20503', 'CGND-HDA-01021', 'CGND-HDA-03977', 'HG01697', 'HG00190', 'CGND-HDA-02762', 'NA12144', 'CGND-HDA-00565', 'HG00158', 'HG00148', 'NA20541', 'CGND-HDA-02756', 'HG01528', 'CGND-HDA-01651', 'HG00236', 'NA20536', 'CGND-HDA-01594', 'HG02235', 'NA20532', 'HG01530', 'NA20586', 'CGND-HDA-02445', 'HG00096', 'CGND-HDA-01454', 'CGND-HDA-02567', 'NA20533', 'CGND-HDA-03790', 'NA12878', 'NA20769', 'CGND-HDA-01427', 'NA20527', 'HG02224', 'HG00244', 'CGND-HDA-03421', 'NA20798', 'CGND-HDA-03785', 'CGND-HDA-00556', 'NA12383', 'HG01791', 'HG00232', 'CGND-HDA-02734', 'HG01619', 'CGND-HDA-01519', 'NA12716', 'HG00146', 'CGND-HDA-00260', 'NA06986', 'NA11881', 'HG00234', 'CGND-HDA-02513', 'CGND-HDA-03763', 'HG01676', 'CGND-HDA-01541', 'NA20761', 'HG01624', 'NA12400', 'CGND-HDA-03793', 'NA11918', 'CGND-HDA-01456', 'HG00174', 'CGND-HDA-02838', 'HG01608', 'CGND-HDA-03781', 'NA12046', 'NA20804', 'CGND-HDA-03481', 'HG01704', 'NA20543', 'CGND-HDA-02718', 'CGND-HDA-03084', 'CGND-HDA-01430', 'CGND-HDA-02327', 'HG01700', 'CGND-HDA-03581', 'CGND-HDA-02446', 'NA20762', 'HG01686', 'CGND-HDA-03768', 'HG01334', 'NA20521', 'CGND-HDA-03858', 'CGND-HDA-02857', 'HG01694', 'HG00116', 'CGND-HDA-03074', 'CGND-HDA-02183', 'NA11894', 'HG01757', 'NA20795', 'CGND-HDA-03978', 'CGND-HDA-02728', 'NA12272', 'NA06994', 'NA07357', 'CGND-HDA-00434', 'NA20535', 'HG00240', 'NA20764', 'CGND-HDA-01503', 'HG01626', 'CGND-HDA-03079', 'HG01628', 'CGND-HDA-03585', 'CGND-HDA-03479', 'CGND-HDA-01447', 'CGND-HDA-01608', 'CGND-HDA-01453', 'NA20542', 'CGND-HDA-03671', 'CGND-HDA-01592', 'HG01766', 'HG00105', 'CGND-HDA-02509', 'CGND-HDA-

17:54:45.641 | INFO    | Flow run 'agile-piculet' - Filtered 1428 alleles with frequency below 5.000%

17:54:45.643 | INFO    | Flow run 'agile-piculet' - Kept 54 alleles

17:54:45.716 | INFO    | Flow run 'agile-piculet' - Finished in state Completed()


clinical data:
                       Quote    Data File ID ExternalSubjectId   
ExternalSampleId                                                 
CGND-HDA-05557    CGND_14852  CGND-HDA-05557       NEUUF013XXL  \
CGND-HDA-05556    CGND_14852  CGND-HDA-05556       NEUHM496PGR   
CGND-HDA-05555    CGND_14852  CGND-HDA-05555       NEUPK599KHH   
CGND-HDA-05554    CGND_14852  CGND-HDA-05554       NEUHD589CVP   
CGND-HDA-05553    CGND_14852  CGND-HDA-05553       NEUXX223WT8   

                              Project     Site Sample Collected   
ExternalSampleId                                                  
CGND-HDA-05557    ALS Natural History  Henry Ford Health System  \
CGND-HDA-05556    ALS Natural History  Henry Ford Health System   
CGND-HDA-05555    ALS Natural History  Henry Ford Health System   
CGND-HDA-05554    ALS Natural History  Henry Ford Health System   
CGND-HDA-05553    ALS Natural History  Henry Ford Health System   

                   Site Specimen Collected     Sex 

## Evaluate model stack

In [14]:
from sklearn.model_selection import StratifiedKFold
from sklearn.calibration import CalibrationDisplay
from sklearn.metrics import RocCurveDisplay, roc_auc_score, auc
from sklearn.preprocessing import MinMaxScaler
from skopt.plots import plot_convergence

from skopt import BayesSearchCV

from fastnumbers import check_real

from types import SimpleNamespace
import matplotlib.pyplot as plt
from matplotlib.gridspec import GridSpec

import asyncio

import neptune
from neptune.types import File

import shap

import plotly.express as px

from inspect import isclass
from io import StringIO
import traceback

# stop API errors when awaiting results
# !prefect config set PREFECT_RESULTS_PERSIST_BY_DEFAULT=True

@task()
def getFeatureImportances(model, data, featureLabels):
  """Get feature importances from fitted model and create SHAP explainer"""
  if model.__class__.__name__ == "MultinomialNB":
    modelCoefficientDF = pd.DataFrame()
    for i, c in enumerate(model.feature_count_[0] if len(model.feature_count_.shape) > 1 else model.feature_count_):
      modelCoefficientDF.loc[i, f"feature_importances_{config['clinicalTable']['controlAlias']}"] = model.feature_log_prob_[0][i]
      modelCoefficientDF.loc[i, f"feature_importances_{config['clinicalTable']['caseAlias']}"] = model.feature_log_prob_[1][i]
  elif hasattr(model, "coef_"):
    modelCoefficientDF = pd.DataFrame()
    if len(model.coef_.shape) > 1:
      try:
        modelCoefficientDF[f"feature_importances_{config['clinicalTable']['controlAlias']}"] = model.coef_[0]
        modelCoefficientDF[f"feature_importances_{config['clinicalTable']['caseAlias']}"] = model.coef_[1]
      except IndexError:
        modelCoefficientDF[f"feature_importances"] = model.coef_[0]                 
    else:
      modelCoefficientDF[f"feature_importances"] = model.coef_[0]
  elif hasattr(model, "feature_importances_"):
    modelCoefficientDF = pd.DataFrame()
    modelCoefficientDF[f"feature_importances"] = model.feature_importances_
  else:
    modelCoefficientDF = None

  if type(modelCoefficientDF) == pd.DataFrame:
      modelCoefficientDF.index = featureLabels
      modelCoefficientDF.index.name = "features"
      
  if config['model']['calculateShapelyExplanations']:
    # Cluster correlated and hierarchical features using masker
    masker = shap.maskers.Partition(data, clustering="correlation")
    shapExplainer = shap.explainers.Permutation(
      model.predict_proba if hasattr(model, "predict_proba") 
      else model.predict, 
      masker, 
      feature_names=["_".join(label)
        for label in featureLabels])
    shapValues = shapExplainer(data)
  else:
    shapExplainer = None
    shapValues = None
    masker = None
  return modelCoefficientDF, shapValues, shapExplainer, masker


@task()
async def plotCalibration(title, labelsPredictionsByInstance):
  # code from https://scikit-learn.org/stable/auto_examples/calibration/plot_calibration_curve.html
  fig, ax_calibration_curve = plt.subplots(figsize=(10, 10))
  colors = plt.cm.get_cmap("Dark2")

  calibration_displays = {}
  for i, (name, (labels, predictions)) in enumerate(labelsPredictionsByInstance.items()):
      display = CalibrationDisplay.from_predictions(
          [config["clinicalTable"]["caseAlias"] if label == 1 else label 
            for label in labels],
          predictions,
          pos_label=config["clinicalTable"]["caseAlias"],
          n_bins=10,
          name=name,
          ax=ax_calibration_curve,
          color=colors(i),
      )
      calibration_displays[name] = display

  ax_calibration_curve.grid()
  ax_calibration_curve.set_title(title)

  # Add histogram
  # grid_positions = [(i+2,j) for i in range(len(predictionsByModelName.keys())//2) for j in range(2)]
  # for i, modelName in enumerate(predictionsByModelName.keys()):
  #     row, col = grid_positions[i]
  #     ax = fig.add_subplot(gs[row, col])
  #     ax.hist(
  #         calibration_displays[modelName].y_prob,
  #         range=(0, 1),
  #         bins=10,
  #         label=modelName,
  #         color=colors(i),
  #     )
  #     ax.set(title=modelName, xlabel="Mean predicted probability", ylabel="Count")

  plt.tight_layout()
  return fig

@task()
async def plotAUC(title, labelsPredictionsByInstance):
  # trace AUC for each set of predictions
  tprs = []
  aucs = []
  mean_fpr = np.linspace(0, 1, 100)

  fig, ax = plt.subplots(figsize=(10, 10))
  for name, (labels, predictions) in labelsPredictionsByInstance.items():
    # plot ROC curve for this fold
    viz = RocCurveDisplay.from_predictions([
                          config["clinicalTable"]["caseAlias"] if label == 1 else label 
                          for label in labels], 
                        predictions,
                        name=name,
                        pos_label=config["clinicalTable"]["caseAlias"],
                        alpha=0.6, lw=2, ax=ax)
    interp_tpr = np.interp(mean_fpr, viz.fpr, viz.tpr)
    interp_tpr[0] = 0.0
    tprs.append(interp_tpr)
    aucs.append(viz.roc_auc)
    
  # summarize ROCs per fold and plot standard deviation
  ax.plot([0, 1], [0, 1], linestyle='--', lw=2, color='r',
      label='Chance', alpha=.8)
  mean_tpr = np.mean(tprs, axis=0)
  mean_tpr[-1] = 1.0
  mean_auc = auc(mean_fpr, mean_tpr)
  std_auc = np.std(aucs)
  ax.plot(mean_fpr, mean_tpr, color='b',
          label=r'Mean ROC (AUC = %0.2f $\pm$ %0.2f)' % (mean_auc, std_auc),
          lw=4, alpha=.8)
  std_tpr = np.std(tprs, axis=0)
  tprs_upper = np.minimum(mean_tpr + std_tpr, 1)
  tprs_lower = np.maximum(mean_tpr - std_tpr, 0)
  ax.fill_between(mean_fpr, tprs_lower, tprs_upper, color='grey', alpha=.2,
                  label=r'$\pm$ 1 std. dev.')

  ax.set(xlim=[-0.05, 1.05], ylim=[-0.05, 1.05],
        title=title)
  ax.legend(loc="lower right")
  ax.set(title=title)
  return fig


@task()
async def plotConfusionMatrix():
  pass

@task()
async def plotSampleAccuracy():
  pass

@task()
async def plotOptimizer(title, resultsByInstance):
  # code from https://scikit-learn.org/stable/auto_examples/calibration/plot_calibration_curve.html
  fig = plt.figure(figsize=(10, 10))
  gs = GridSpec(2, 2)
  colors = plt.cm.get_cmap("Dark2")
  ax_convergence = fig.add_subplot(gs[:2, :2])
  plot_convergence(*[
    (modelName, result) for modelName, result in resultsByInstance.items()], 
    ax=ax_convergence, color=colors)
  ax_convergence.set(title=title)
  plt.tight_layout()
  return fig

@task()
def prepareDatasets(caseGenotypes, controlGenotypes, verbose=True):
    caseIDs = caseGenotypes.columns
    controlIDs = controlGenotypes.columns
    # store number of cases & controls
    caseControlCounts = [len(caseIDs), len(controlIDs)]
    # determine which has more samples
    labeledIDs = [caseIDs, controlIDs]
    majorIDs = labeledIDs[np.argmax(caseControlCounts)]
    minorIDs = labeledIDs[np.argmin(caseControlCounts)]
    # downsample larger group to match smaller group
    majorIndex = np.random.choice(np.arange(len(majorIDs)), min(caseControlCounts), replace=False)
    
    excessMajorIDs, balancedMajorIDs = [], []
    for index, id in enumerate(majorIDs):
      if index in majorIndex:
        balancedMajorIDs.append(id)
      else:
        excessMajorIDs.append(id)
    
    allGenotypes = pd.concat([caseGenotypes, controlGenotypes], axis=1)
    
    genotypeExcessIDs, crossValGenotypeIDs = [], []
    # match IDs between genotype and clinical data; dataframe labels have label suffixes
    unmatchedTrainIDs = balancedMajorIDs + minorIDs
    for label in tqdm(allGenotypes.columns, desc="Matching IDs", unit="ID"):
      for setType in ["excess", "train"]:
        idSet = excessMajorIDs if setType == "excess" else unmatchedTrainIDs
        for i, id in enumerate(idSet):
          if (id in label) or (label in id): 
            if setType == "train":
              if label not in crossValGenotypeIDs: crossValGenotypeIDs.append(label)
            elif setType == "excess":
              if label not in genotypeExcessIDs: genotypeExcessIDs.append(label)
            idSet = np.delete(idSet, i)
            break
          
    if verbose:
      print(f"\n{len(crossValGenotypeIDs)} for training:\n{crossValGenotypeIDs}")
      print(f"\n{len(genotypeExcessIDs)} are excess:\n{genotypeExcessIDs}")
      print(f"\nVariant count: {len(allGenotypes.index)}")
      
    samples = allGenotypes.loc[:, crossValGenotypeIDs].dropna(how='any')  # drop variants with missing values
    excessMajorSamples = allGenotypes.loc[:, genotypeExcessIDs]

    variantIndex = list(samples.index)
    pass
    scaler = MinMaxScaler()
    embedding = {
        'sampleIndex': crossValGenotypeIDs,
        'labels': np.array([1 if id in caseIDs else 0 for id in crossValGenotypeIDs]),
        'samples': scaler.fit_transform(samples).transpose(), # samples are now rows (samples, variants)
        'excessMajorIndex': genotypeExcessIDs,
        'excessMajorLabels': [1 if id in caseIDs else 0 for id in genotypeExcessIDs],
        'excessMajorSamples': scaler.fit_transform(excessMajorSamples).transpose(),
        'variantIndex': variantIndex,
    }
    return embedding
  
@task()
def optimizeHyperparameters(samples, labels, model, parameterSpace, cvIterator, metricFunction, n_jobs=1):
  # hyperparameter search (inner cross-validation)
  optimizer = BayesSearchCV(
    model, parameterSpace, cv=cvIterator, n_jobs=n_jobs, n_points=4,
    return_train_score=True, n_iter=100, scoring=metricFunction)
  # train / optimize parameters
  optimizer.fit(samples, labels)
  return optimizer

def serializeDataFrame(dataframe):
  stream = StringIO()
  dataframe.to_csv(stream)
  return File.from_stream(stream, extension='csv')

@task()
async def beginTracking(model, runNumber, embedding, clinicalData, deserializedIDs):
  runTracker = neptune.init_run(project=f'{config["tracking"]["entity"]}/{config["tracking"]["project"]}', api_token=config['tracking']['token'])
  runTracker['sys/tags'].add(model.__class__.__name__)
  runTracker['bootstrapIteration'] = runNumber+1
  runTracker["config"] = {key: (item if check_real(item) or isinstance(item, str) else str(item)) for key, item in config.items()}
  
  embeddingDF = pd.DataFrame(data=embedding["samples"], columns=embedding["variantIndex"], index=embedding["sampleIndex"])
  embeddingDF.index.name = "id"
  runTracker['embedding'].upload(serializeDataFrame(embeddingDF))
  runTracker['clinicalData'].upload(serializeDataFrame(clinicalData.loc[clinicalData.index.isin(deserializedIDs)]))
  
  runTracker['nVariants'] = len(embedding["variantIndex"])
  runID = runTracker["sys/id"].fetch()
  runTracker.stop()
  return runID

@task()
async def trackResults(runID, current):
  runTracker = neptune.init_run(project=f'{config["tracking"]["entity"]}/{config["tracking"]["project"]}', with_id=runID, api_token=config['tracking']['token'])
  if config['model']['hyperparameterOptimization']:
      runTracker["modelParams"] = {k+1: current["fittedOptimizers"][k].best_params_ for k in range(config['sampling']['crossValIterations'])}

  runTracker["sampleResults"].upload(serializeDataFrame(pd.DataFrame.from_dict({
      "probability": [probability[1] for foldResults in current["probabilities"] for probability in foldResults], 
      "id": [id for foldResults in current["testIDs"] for id in foldResults]}, dtype=object).set_index("id")))
  
  if config['model']['calculateShapelyExplanations']:
    runTracker['shapExplanationsPerFold'].upload(File.as_pickle(current["localExplanations"]))
    runTracker['shapExplainersPerFold'].upload(File.as_pickle(current["shapExplainers"]))
    runTracker['shapMaskersPerFold'].upload(File.as_pickle(current["shapMaskers"]))
    runTracker["featureImportance/shapelyExplanations/average"].upload(serializeDataFrame(current['averageShapelyValues']))
 
  if current["globalExplanations"][0] is not None:
    runTracker[f"featureImportance/modelCoefficients/average"].upload(
      serializeDataFrame(current["averageGlobalExplanations"]))
 
  for k in range(config['sampling']['crossValIterations']):
    testLabelsSeries = pd.Series(current["testLabels"][k], name='testLabel')
    trainLabelsSeries = pd.Series(current["trainLabels"][k], name='trainLabel')
    testLabelsSeries.index = current["testIDs"][k]
    testLabelsSeries.index.name = "id"
    trainLabelsSeries.index = current["trainIDs"][k]
    trainLabelsSeries.index.name = "id"
    runTracker[f'trainIDs/{k+1}'].upload(serializeDataFrame(pd.Series(current["trainIDs"][k])))
    runTracker[f'testIDs/{k+1}'].upload(serializeDataFrame(pd.Series(current["testIDs"][k])))
    runTracker[f'testLabels/{k+1}'].upload(serializeDataFrame(pd.Series(testLabelsSeries)))
    runTracker[f'trainLabels/{k+1}'].upload(serializeDataFrame(pd.Series(trainLabelsSeries)))
    if current["globalExplanations"][k] is not None:
      runTracker[f"featureImportance/modelCoefficients/{k+1}"].upload(serializeDataFrame(current["globalExplanations"][k]))
    if config['model']['calculateShapelyExplanations']:
      runTracker[f"featureImportance/shapelyExplanations/{k+1}"].upload(serializeDataFrame(pd.DataFrame.from_dict({
        "feature_name": [name for name in current['localExplanations'][0].feature_names],
        "value": [np.mean(current['localExplanations'][k].values[featureIndex])
          for featureIndex in range(len(current['localExplanations'][0].feature_names))]
        }, dtype=object).set_index("feature_name")))
  
  runTracker["meanAUC"] = np.mean(current["testAUC"])
  # average sample count across folds
  runTracker['nTrain'] = np.mean([len(idList) for idList in current["trainIDs"]])
  runTracker['nTest'] = np.mean([len(idList) for idList in current["testIDs"]])
  runTracker.stop()
      
# parallel task runner patch https://github.com/PrefectHQ/prefect/issues/7319
# TODO build task runners only 
async def build_subflow(name, args):
  
  if name == 'classify':
    @flow(
      task_runner=RayTaskRunner(
      init_kwargs={'address': parallelRunner.address_info['address'], 'configure_logging': True, 'logging_level': logging.WARN}
    ))
    async def classify(model, parameterSpace, innerCvIterator, outerCvIterator):
      results = {}
      results['samples'] = {}
      results['labels'] = {}
      results['model'] = model.__class__.__name__
      for runNumber in range(config['sampling']['bootstrapIterations']):   
        trainIDs = set()
        testIDs = set()
        results[runNumber] = {}
        embedding = prepareDatasets(caseGenotypes, controlGenotypes, verbose=(True if runNumber == 0 else False))
        deserializedIDs = list()
        for id in embedding['sampleIndex']:
          deserializedIDs.extend(id.split("__"))
        totalSampleCount = len(embedding['samples'])
        caseCount = np.count_nonzero(embedding['labels'])
        print(f"{totalSampleCount} samples\n")
        print(f"{caseCount} cases\n")
        print(f"{totalSampleCount - caseCount} controls\n")
        current = {}
        # check if model is initialized
        if isclass(model):
          if model.__name__ == 'TabNetClassifier':
            model = model(verbose=False, optimizer_fn=Lion)
        print(f"Iteration {runNumber+1} with model {model.__class__.__name__}")
        runID = await beginTracking.submit(model, runNumber, embedding, clinicalData, deserializedIDs)
        # outer cross-validation
        crossValIndices = np.array([
            (cvTrainIndices, cvTestIndices) 
            for (cvTrainIndices, cvTestIndices) in outerCvIterator.split(embedding['samples'], embedding['labels'])])
        current["trainIndices"] = crossValIndices[:,0]
        current["testIndices"] = crossValIndices[:,1]
        trainIDs.update(*[np.array(embedding['sampleIndex'])[indices] for indices in current["trainIndices"]])
        testIDs.update(*[np.array(embedding['sampleIndex'])[indices] for indices in current["testIndices"]])
        outerCrossValResults = zip(*await asyncio.gather(
          *[build_subflow('evaluate', (
              trainIndices, testIndices, model, embedding['labels'], embedding['samples'], embedding['variantIndex'], embedding['sampleIndex'], parameterSpace, innerCvIterator))
            for trainIndices, testIndices in zip(current["trainIndices"], current["testIndices"])
          ]))
        resultNames = ["globalExplanations", "localExplanations", "probabilities", "predictions", "testLabels", "trainLabels", "trainIDs", "testIDs", "fittedOptimizers", "shapExplainers", "shapMaskers"]
        current = {**current, **{name: result for name, result in zip(resultNames, outerCrossValResults)}}
        current["testAUC"] = [roc_auc_score(labels, (probabilities[:,1] if len(probabilities.shape) > 1 else probabilities))
          for labels, probabilities in zip(current["testLabels"], current["probabilities"])]
        
        if config['model']['calculateShapelyExplanations']:
          current['averageShapelyValues'] = pd.DataFrame.from_dict({
            "feature_name": [name for name in current['localExplanations'][0].feature_names],
            "value": [np.mean(
              np.hstack([np.mean(localExplanations.values[:,featureIndex]) for localExplanations in current['localExplanations']])
              ) for featureIndex in range(len(current['localExplanations'][0].feature_names))]
            }, dtype=object).set_index("feature_name")
          
        if current['globalExplanations'][0] is not None:
          current['averageGlobalExplanations'] = pd.concat(current["globalExplanations"]).reset_index().groupby("features").mean()
        
        caseAccuracy = np.mean([np.divide(np.count_nonzero(labels==predictions), len(labels)) for predictions, labels in zip(current["predictions"], current["testLabels"])])
        controlAccuracy = 1 - caseAccuracy
        await trackResults.submit(runID, current)
        
        # plot AUC & hyperparameter convergence
        plotSubtitle = f"""
              {config["tracking"]["name"]}, {embedding["samples"].shape[1]} variants
              Minor allele frequency over {'{:.1%}'.format(config['vcfLike']['minAlleleFrequency'])}
              
              {np.count_nonzero(embedding['labels'])} {config["clinicalTable"]["caseAlias"]}s @ {'{:.1%}'.format(caseAccuracy)} accuracy, {len(embedding['labels']) - np.count_nonzero(embedding['labels'])} {config["clinicalTable"]["controlAlias"]}s @ {'{:.1%}'.format(controlAccuracy)} accuracy
              {int(np.around(np.mean([len(indices) for indices in current["trainIndices"]])))}±1 train, {int(np.around(np.mean([len(indices) for indices in current["testIndices"]])))}±1 test samples per x-val fold"""
        results[runNumber] = current
        
        # record sample metrics
        for fold in range(config['sampling']['crossValIterations']):
          for j, sampleID in enumerate(current['testIDs'][fold]):
            try:
              results['samples'][sampleID].append(current["probabilities"][fold][j])
            except KeyError:
              results['samples'][sampleID] = [current["probabilities"][fold][j]]
            finally:
              results['labels'][sampleID] = current["testLabels"][fold][j]
            
        await build_subflow('trackVisualizations', (runID, plotSubtitle, model.__class__.__name__, current))
      
        results[runNumber]['testCount'] = len(trainIDs)
        results[runNumber]['trainCount'] = len(testIDs)
      return results
    return await classify(*args)
  
  elif name == 'evaluate':
  
    @flow()
    async def evaluate(trainIndices, testIndices, model, labels, samples, variantIndex, sampleIndex, parameterSpace, cvIterator):
      if config['model']['hyperparameterOptimization']:
        fittedOptimizer = optimizeHyperparameters(
            samples[trainIndices], labels[trainIndices], model, 
            parameterSpace, cvIterator, 'neg_mean_squared_error')
        model.set_params(**fittedOptimizer.best_params_)
      else:
        fittedOptimizer = None
      model.fit(samples[trainIndices], labels[trainIndices])
      try:
        probabilities = model.predict_proba(samples[testIndices])
      except AttributeError:
        probabilities = model.predict(samples[testIndices])
        if len(probabilities.shape) <= 1:
          probabilities = np.array([[1 - p, p] for p in probabilities])
      predictions = np.argmax(probabilities, axis=1)
      modelValues, shapValues, shapExplainer, shapMasker = getFeatureImportances(
        model, samples[testIndices], variantIndex)
      globalExplanations = modelValues
      localExplanations = shapValues
      trainLabels = np.array(labels[trainIndices])
      testLabels = np.array(labels[testIndices])
      trainIDs = np.array([sampleIndex[i] for i in trainIndices]) 
      testIDs = np.array([sampleIndex[i] for i in testIndices])
      return globalExplanations, localExplanations, probabilities, predictions, testLabels, trainLabels, trainIDs, testIDs, fittedOptimizer, shapExplainer, shapMasker
    return await evaluate(*args)
  
  elif name == 'trackVisualizations':
  
    @flow(task_runner=ConcurrentTaskRunner())
    async def trackVisualizations(runID, plotSubtitle, modelName, current):
      runTracker = neptune.init_run(project=f'{config["tracking"]["entity"]}/{config["tracking"]["project"]}', with_id=runID, api_token=config['tracking']['token'])
      runTracker['plots/aucPlot'] = await plotAUC.submit(f"""
          Receiver Operating Characteristic (ROC) Curve
          {modelName} with {config['sampling']['crossValIterations']}-fold cross-validation
          {plotSubtitle}
          """,
          {f"Fold {k+1}": (current["testLabels"][k], np.array(current["probabilities"][k])[:,1])
            if len(current["probabilities"][k][0].shape) >= 1 
            else (current["testLabels"][k], current["probabilities"][k]) 
            for k in range(config['sampling']['crossValIterations'])},
          )
      if config['model']['hyperparameterOptimization']:
        runTracker['plots/convergencePlot'] = await plotOptimizer.submit(f"""
          Hyperparameter convergence, mean squared error
          {modelName} with {config['sampling']['crossValIterations']}-fold cross-validation
          {plotSubtitle}
          """,
          {f"Fold {k+1}": [result for result in current["fittedOptimizers"][k].optimizer_results_]
          for k in range(config['sampling']['crossValIterations'])},
          )
      
      # plot shapely feature importance
      if config['model']['calculateShapelyExplanations']:
        for j in range(config["sampling"]["crossValIterations"]):
          localExplanations = current["localExplanations"][j]
          caseExplanations = localExplanations
          caseExplanations.values = caseExplanations.values[:,:,1] if len(caseExplanations.values.shape) > 2 else caseExplanations.values
          heatmap = plt.figure()
          plt.title(f"""
            Shapely explanations from {modelName}
            Fold {j+1}
            {plotSubtitle}
            """) 
          shap.plots.heatmap(caseExplanations, show=False)
          runTracker[f"plots/featureHeatmap/{j+1}"] = heatmap
          plt.close(heatmap)
          labelsProbabilities = ((current["testLabels"][j], np.array(current["probabilities"][j])[:,1])
            if len(current["probabilities"][j][0].shape) >= 1 
            else (current["testLabels"][j], current["probabilities"][j]))
          stdDeviation = np.std((labelsProbabilities[1] - labelsProbabilities[0])**2)
          for k in range(len(current["testIDs"][j])):
            probability = labelsProbabilities[1][k] if isinstance(labelsProbabilities[1][k], np.ndarray) else labelsProbabilities[1][k]
            label = labelsProbabilities[0][k] if isinstance(labelsProbabilities[0][k], np.ndarray) else labelsProbabilities[0][k]
            if config['tracking']['plotAllSampleImportances'] or np.absolute((probability - label)**2) <= stdDeviation:
              sampleID=current['testIDs'][j][k]
              waterfallPlot = plt.figure()
              plt.title(f"""
                {sampleID}
                Shapely explanations from {modelName}
                Fold {j+1}
                {plotSubtitle}
                """)
              # patch parameter bug: https://github.com/slundberg/shap/issues/2362
              to_pass = SimpleNamespace(**{
                              'values': localExplanations[k].values,
                              'data': localExplanations[k].data,
                              'display_data': None,
                              'feature_names': localExplanations.feature_names,
                              'base_values': localExplanations[k].base_values[current['testLabels'][j][k]] if len(localExplanations[k].base_values.shape) == 1 else localExplanations[k].base_values, 
                })
              shap.plots.waterfall(to_pass, show=False)
              try:
                runTracker[f"plots/samples/{j+1}/{sampleID}"] = waterfallPlot
              except Exception:
                runTracker[f"plots/samples/{j+1}/{sampleID}"] = f"""failed to plot: {traceback.format_exc()}"""
              plt.close(waterfallPlot)
      plt.close('all')
      runTracker.stop()
    await trackVisualizations(*args)
    
@flow(
  task_runner=RayTaskRunner(
    init_kwargs={'address': parallelRunner.address_info['address'], 'configure_logging': True, 'logging_level': logging.WARN}
  ))
async def bootstrapSampling():
  # caseGenotypes, caseIDs, controlGenotypes, controlIDs, clinicalData = await processInputFiles()
  outerCvIterator = StratifiedKFold(n_splits=config['sampling']['crossValIterations'], shuffle=False)
  innerCvIterator = outerCvIterator
  projectTracker = neptune.init_project(project=f'{config["tracking"]["entity"]}/{config["tracking"]["project"]}', api_token=config['tracking']['token'])
  
  results = await asyncio.gather(
    *[build_subflow('classify', (model, hyperparameterSpace, innerCvIterator, outerCvIterator)) 
        for(model, hyperparameterSpace) in list(config['model']['stack'].items())
    ])
  
  labelsProbabilitiesByModelName = dict()
  variantCount = 0
  lastVariantCount = 0
  sampleResults = {}
  
  # asyncio.gather preserves order
  for i, model in enumerate(config['model']['stack']):
    modelName = model.__class__.__name__
    modelResult = results[i]
    
    for sampleID in modelResult['samples'].keys():
      flattenedProbabilities = np.array([
        prediction[1] if len(prediction) >= 2 
        else prediction
        for prediction in modelResult['samples'][sampleID] 
        ]) 
      if sampleID not in sampleResults:
        # label, probability, accuracy
        sampleResults[sampleID] = [
          modelResult['labels'][sampleID], 
          modelResult['samples'][sampleID], 
          np.mean([np.around(caseProbability) == modelResult['labels'][sampleID] 
                            for caseProbability in flattenedProbabilities])
          ]
      else:
        sampleResults[sampleID][1].append(modelResult['samples'][sampleID])
        sampleResults[sampleID][2] = np.mean([sampleResults[sampleID][2], np.mean([np.around(caseProbability) == modelResult['labels'][sampleID] 
                              for caseProbability in flattenedProbabilities])])
    
    if modelName not in labelsProbabilitiesByModelName: labelsProbabilitiesByModelName[modelName] = [[], []]
    globalExplanationsList = []
    for j in range(config['sampling']['bootstrapIterations']):
      bootstrapResult = modelResult[j]
      # append labels
      labelsProbabilitiesByModelName[modelName][0] = np.hstack(
        (labelsProbabilitiesByModelName[modelName][0],
        *bootstrapResult["testLabels"]))
      # append probabilities
      labelsProbabilitiesByModelName[modelName][1] = np.hstack(
        [labelsProbabilitiesByModelName[modelName][1], 
        np.concatenate(bootstrapResult["probabilities"])[:,1]
          if len(bootstrapResult["probabilities"][0].shape) >= 1
          else np.concatenate(bootstrapResult["probabilities"])])
        
      if not isinstance(bootstrapResult['globalExplanations'][0], pd.DataFrame): continue
      variantCount = bootstrapResult["globalExplanations"][0].shape[0]
      assert lastVariantCount == variantCount or lastVariantCount == 0
      lastVariantCount = variantCount
  
      globalExplanationsList += bootstrapResult["globalExplanations"]
    
    if globalExplanationsList:
      averageGlobalExplanationsDataFrame = pd.concat(globalExplanationsList).reset_index().groupby("features").mean()
      projectTracker[f"averageModelCoefficients/{modelName}"].upload(serializeDataFrame(averageGlobalExplanationsDataFrame))

  sampleResultsDataFrame = pd.DataFrame.from_dict(sampleResults, orient="index", columns=["label", "probability", "accuracy"])
  sampleResultsDataFrame.index.name = "id"

  projectTracker["sampleResults"].upload(serializeDataFrame(sampleResultsDataFrame))
  projectTracker["sampleResultsObject"].upload(File.as_pickle(sampleResultsDataFrame))
  
  if config['model']['calculateShapelyExplanations']:
    averageShapelyExplanationsDataFrame = pd.concat(
      [modelResult[j]['averageShapelyValues'] 
      for j in range(config['sampling']['bootstrapIterations'])]
      ).reset_index().groupby("feature_name").mean()
    projectTracker["averageShapelyExplanations"].upload(serializeDataFrame(averageShapelyExplanationsDataFrame))

  caseAccuracy = sampleResultsDataFrame[sampleResultsDataFrame["label"] == 1]["accuracy"].mean()
  controlAccuracy = 1 - caseAccuracy
  
  bootstrapTrainCount = int(np.around(np.mean([modelResult[j]['trainCount'] for j in range(config['sampling']['bootstrapIterations'])])))
  bootstrapTestCount = int(np.around(np.mean([modelResult[j]['testCount'] for j in range(config['sampling']['bootstrapIterations'])])))
 
  plotSubtitle = f"""
  {config['sampling']['crossValIterations']}x cross-validation over {config['sampling']['bootstrapIterations']} bootstrap iterations
  {config["tracking"]["name"]}, {variantCount} variants
  Minor allele frequency over {'{:.1%}'.format(config['vcfLike']['minAlleleFrequency'])}
  
  {sampleResultsDataFrame['label'].value_counts()[1]} cases @ {'{:.1%}'.format(caseAccuracy)} accuracy, {sampleResultsDataFrame['label'].value_counts()[0]} controls @ {'{:.1%}'.format(controlAccuracy)} accuracy
  {bootstrapTrainCount}±1 train, {bootstrapTestCount}±1 test samples per bootstrap iteration"""

  projectTracker["sampleAccuracyPlot"].upload(px.histogram(
    sampleResultsDataFrame, x='accuracy', color='label', pattern_shape='label', range_x=[0,1],
    title=f"""Mean sample accuracy, {config['sampling']['crossValIterations']}x cross-validation over {config['sampling']['bootstrapIterations']} bootstrap iterations"""))

  projectTracker["aucPlot"].upload(plotAUC(f"""
    Receiver Operating Characteristic (ROC) Curve
    {plotSubtitle}
    """,
    labelsProbabilitiesByModelName,
    ))
  
  projectTracker["calibrationPlot"].upload(File.as_image(plotCalibration(f"""
    Calibration Curve
    {plotSubtitle}
    """,
    labelsProbabilitiesByModelName,
    )))
  
  if config['model']['hyperparameterOptimization']:
    projectTracker["convergencePlot"].upload(File.as_image(plotOptimizer(f"""
      Convergence Plot
      {plotSubtitle}
      """,
      {modelName: [result
                  for j in range(config['sampling']['bootstrapIterations'])
                  for foldOptimizer in results[i][j]["fittedOptimizers"]
                  for result in foldOptimizer.optimizer_results_
                  ] 
        for i, modelName in enumerate(config['model']['stack'])
      })))
  
  projectTracker.stop()
  return results

results = await bootstrapSampling()

17:54:45.912 | INFO    | prefect.engine - Created flow run 'cherry-raven' for flow 'bootstrapSampling'

17:54:45.914 | INFO    | prefect.task_runner.ray - Local Ray instance is already initialized. Using existing local instance.

https://new-ui.neptune.ai/ejmockler/ALS-NUPS-NonBinarized/


17:54:46.874 | INFO    | Flow run 'cherry-raven' - Created subflow run 'attentive-raptor' for flow 'classify'

17:54:46.876 | INFO    | prefect.task_runner.ray - Local Ray instance is already initialized. Using existing local instance.

...

18:32:19.119 | INFO    | Task run 'prepareDatasets-13' - Finished in state Completed()

1368 samples

684 cases

684 controls

Iteration 14 with model LogisticRegression


18:32:19.157 | INFO    | Flow run 'cherubic-eagle' - Created task run 'beginTracking-13' for task 'beginTracking'

18:32:19.159 | INFO    | Flow run 'cherubic-eagle' - Executing 'beginTracking-13' immediately...

https://new-ui.neptune.ai/ejmockler/ALS-NUPS-NonBinarized/e/ALSNONBIN-168
Shutting down background jobs, please wait a moment...
Done!
Waiting for the remaining 12 operations to synchronize with Neptune. Do not kill this process.
